In [19]:
!pip install bar-chart-race

### LIBRARYS

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import bar_chart_race as bcr

### DATAFRAMES

In [2]:
df = pd.read_csv("premierLeague_1992-2017.csv")
extend = pd.read_csv("df_full_premierleague.csv")

### FUNÇÕES

In [16]:
def OrderDate(df):
      return df.sort_values(by=['date'], inplace=True)


def correctDateHome(dateStr):
    strList = dateStr.split("-")
    if strList[0] > strList[1]:
        return 3
    elif strList[0] == strList[1]:
        return 1
    else:
        return 0

def correctDateAway(dateStr):
    strList = dateStr.split("-")
    if strList[0] > strList[1]:
        return 0
    elif strList[0] == strList[1]:
        return 1
    else:
        return 3

def correctDateHomeTwo(tab, taba):
    if tab > taba:
        return 3 
    elif tab == taba:
        return 1
    else:
        return 0

def correctDateAwayTwo(tab, taba):
    if tab > taba:
        return 0
    elif tab == taba:
        return 1
    else:
        return 3
    
def DateFilter(df,date):
    depois = df['date'] > date
    filtro = df.loc[depois]
    return filtro



### Order By Date

We order dataframe to cronological date

In [4]:
OrderDate(df)
OrderDate(extend)

### CREATE POINTS COLUMNS

Vamos verificar os resultados da partida para saber se houve vencedor ou não, nesse caso criaremos 2 colunas ("PointsH" e "PointsA") inserir a pontuação que a equipe da casa e a visitante fez na partida

In [5]:
extend["PointsH"] = extend["result_full"].apply(lambda x: correctDateHome(x))
extend["PointsA"] = extend["result_full"].apply(lambda x: correctDateAway(x))
df["PointsH"] = df["result"].apply(lambda x: correctDateHome(x))
df["PointsA"] = df["result"].apply(lambda x: correctDateAway(x))

Agora, selecionamos as colunas especificas e em comum entre os dois dataframes e posteriormente será aplicado a função para 
filtrar o segundo dataframe para ler somente os dados com as datas posteriores à ultima linha do primeiro dataframe. Com
isso feito, podemos efetuar o append para juntar os dois dataframes

In [6]:
extend

Unnamed: 0                                 link_match season  \
55            55   https://www.premierleague.com/match/7087  10/11   
57            57   https://www.premierleague.com/match/7089  10/11   
58            58   https://www.premierleague.com/match/7090  10/11   
59            59   https://www.premierleague.com/match/7091  10/11   
60            60   https://www.premierleague.com/match/7092  10/11   
...          ...                                        ...    ...   
3923        3923  https://www.premierleague.com/match/59157  20/21   
3924        3924  https://www.premierleague.com/match/59158  20/21   
4008        4008  https://www.premierleague.com/match/59164  20/21   
4006        4006  https://www.premierleague.com/match/59160  20/21   
4007        4007  https://www.premierleague.com/match/59161  20/21   

            date                 home_team             away_team result_full  \
55    2010-08-14               Aston Villa       West Ham United         3-0   
57    2010-08-14          Bolton Wanderers                Fulham         0-0   
58    2010-08-14                   Chelsea  West Bromwich Albion         6-0   
59    2010-08-14                Sunderland       Birmingham City         2-2   
60    2010-08-14         Tottenham Hotspur       Manchester City         0-0   
...          ...                       ...                   ...         ...   
3923  2021-03-06  Brighton and Hove Albion        Leicester City         1-2   
3924  2021-03-06                   Burnley               Arsenal         1-1   
4008  2021-03-07      West Bromwich Albion      Newcastle United         0-0   
4006  2021-03-07                 Liverpool                Fulham         0-1   
4007  2021-03-07           Manchester City     Manchester United         0-2   

     result_ht  home_clearances  home_corners  ...  yellow_cards_avg_away  \
55         2-0             24.0          15.0  ...                    NaN   
57         0-0             54.0           4.0  ...                    NaN   
58         2-0             10.0           3.0  ...                    NaN   
59         1-0             49.0           3.0  ...                    NaN   
60         0-0             20.0          10.0  ...                    NaN   
...        ...              ...           ...  ...                    ...   
3923       1-0              5.0           6.0  ...                    1.8   
3924       1-1             16.0           2.0  ...                    1.4   
4008       0-0             21.0           9.0  ...                    1.8   
4006       0-1             13.0           9.0  ...                    1.8   
4007       0-1              7.0           6.0  ...                    1.5   

      goals_scored_ft_avg_away  goals_conced_ft_avg_away  \
55                         NaN                       NaN   
57                         NaN                       NaN   
58                         NaN                       NaN   
59                         NaN                       NaN   
60                         NaN                       NaN   
...                        ...                       ...   
3923                      1.70                      1.15   
3924                      1.31                      1.04   
4008                      1.04                      1.69   
4006                      0.78                      1.22   
4007                      1.96                      1.19   

      sg_match_ft_acum_away  goals_scored_ht_avg_away  \
55                      NaN                       NaN   
57                      NaN                       NaN   
58                      NaN                       NaN   
59                      NaN                       NaN   
60                      NaN                       NaN   
...                     ...                       ...   
3923                   15.0                      0.78   
3924                    7.0                      0.65   
4008                  -17.0                  

In [7]:
extend = extend[["date","home_team", "away_team", "PointsH", "PointsA"]].reset_index(drop=True)
df = df[["date","home_team", "away_team", "PointsH", "PointsA"]].reset_index(drop=True)
extend = DateFilter(extend,"2018-05-15")

In [8]:
df = df.append(extend)

Proximo passo é efetuar o pivottable para que cada time se encaixe em uma coluna e sua pontuação defina-se de acordo com a data em que atuou.Como precisamos dois valores (PointsH e PointsA) para se definir a pontuação no dia, será usado pivot no time da casa, visitante e depois a combinação dos dois. Apos esse passo, ainda vamos substituir os valores NaN por 0 para que conseguimos efetuar a soma nos proximos passos

In [9]:
def pivottableorder(df):
    HomeTable = df.pivot(index = "date", columns = "home_team", values = "PointsH").reset_index().rename_axis(None, axis=1)
    AwayTable = df.pivot(index = "date", columns = "away_team", values = "PointsA").reset_index().rename_axis(None, axis=1)
    TableFull = HomeTable.combine_first(AwayTable)
    TableFull = TableFull.fillna(0)
    TableFull.iloc[:,1:] = TableFull.iloc[:,1:].astype(int)
    TableFull.set_index("date", inplace = True) 
    return TableFull


In [10]:
TableFull = pivottableorder(df)

Efetuamos a soma cumulativa com o ".cumsum" para descobrir a pontuação acumulativa de cada equipe em determinada data

In [11]:
AcumulateTable = TableFull.cumsum(axis = 0)

Opcionalmente podemos selecionar apenas os melhores times para melhor performace do grafico

In [12]:
AcumulateTableS = AcumulateTable.T
AcumulateTableS.sort_values(by=['2021-03-07'], inplace=True, ascending=False)
AcumulateTableS[['2021-03-07']]

date                      2021-03-07
Manchester United               2288
Arsenal                         2049
Chelsea                         2044
Liverpool                       1991
Tottenham Hotspur               1695
Everton                         1522
Manchester City                 1515
Newcastle United                1343
Aston Villa                     1298
West Ham United                 1182
Southampton                     1013
Blackburn Rovers                 970
Leeds United                     727
Leicester City                   722
Middlesbrough                    664
Fulham                           638
Sunderland                       618
Bolton Wanderers                 575
Crystal Palace                   505
West Bromwich Albion             482
Stoke City                       457
Coventry City                    409
Sheffield Wednesday              392
Wimbledon FC                     391
Norwich City                     380
Charlton Athletic                361
Wigan Athletic                   331
Swansea City                     312
Queens Park Rangers              308
Portsmouth                       302
Birmingham City                  301
Wolverhampton Wanderers          287
Burnley                          281
Derby County                     274
Watford                          262
Nottingham Forest                239
Ipswich Town                     224
Sheffield United                 200
Hull City                        171
Brighton and Hove Albion         143
Bournemouth                      132
Reading                          119
Oldham Athletic                   89
AFC Bournemouth                   79
Cardiff City                      64
Bradford City                     62
Huddersfield Town                 53
Blackpool                         39
Barnsley                          35
Swindon Town                      30

## CONSTRUÇÃO DO GRAFICO

In [13]:
bcr.bar_chart_race(df = AcumulateTable, 
                   filename = None,
                   period_label = {'x':.75, 'y': .1},
                   n_bars=6,
                   period_length=200,
                   filter_column_colors = 'True',
                   title = 'Premier League 1992 - 2021')

SyntaxError: invalid syntax (<ipython-input-13-13ebdada84cd>, line 7)

## Criação de Cenarios

Podemos criar uma função, que servirá para filtrar o dataframe para a partir de uma determinada data ou intervalo de datas
Alem disso, podemos já atribuir a soma cumulativa na função

In [20]:
def DateFilter(df,date):
    depois = df.index > date
    filtro = df.loc[depois]
    filtro = filtro.cumsum(axis = 0)
    return filtro

### Premier Era Abramovich

In [22]:
SumScenario = DateFilter(TableFull, "2003-06-01")
SumScenario.head(10)

AFC Bournemouth  Arsenal  Aston Villa  Barnsley  Birmingham City  \
date                                                                           
2003-08-16                0        3            0         0                3   
2003-08-17                0        3            0         0                3   
2003-08-23                0        3            0         0                4   
2003-08-24                0        6            1         0                4   
2003-08-25                0        6            1         0                4   
2003-08-26                0        6            1         0                4   
2003-08-27                0        9            1         0                4   
2003-08-30                0        9            4         0                7   
2003-08-31                0       12            4         0                7   
2003-09-13                0       13            4         0                7   

            Blackburn Rovers  Blackpool  Bolton Wanderers  Bournemouth  \
date                                                                     
2003-08-16                 3          0                 0            0   
2003-08-17                 3          0                 0            0   
2003-08-23                 4          0                 1            0   
2003-08-24                 4          0                 1            0   
2003-08-25                 4          0                 1            0   
2003-08-26                 4          0                 1            0   
2003-08-27                 4          0                 1            0   
2003-08-30                 5          0                 2            0   
2003-08-31                 5          0                 2            0   
2003-09-13                 5          0                 5            0   

            Bradford City  ...  Sunderland  Swansea City  Swindon Town  \
date                       ...                                           
2003-08-16              0  ...           0             0             0   
2003-08-17              0  ...           0             0             0   
2003-08-23              0  ...           0             0             0   
2003-08-24              0  ...           0             0             0   
2003-08-25              0  ...           0             0             0   
2003-08-26              0  ...           0             0             0   
2003-08-27              0  ...           0             0             0   
2003-08-30              0  ...           0             0             0   
2003-08-31              0  ...           0             0             0   
2003-09-13              0  ...           0             0             0   

            Tottenham Hotspur  Watford  West Bromwich Albion  West Ham United  \
date                                                                            
2003-08-16                  0        0                     0                0   
2003-08-17                  0        0                     0                0   
2003-08-23                  3        0                     0                0   
2003-08-24                  3        0                     0                0   
2003-08-25                  3        0                     0                0   
2003-08-26                  3        0                     0                0   
2003-08-27                  4        0                     0                0   
2003-08-30                  4        0                     0                0   
2003-08-31                  4        0                     0                0   
2003-09-13                  4        0                     0                0   

            Wigan Athletic  Wimbledon FC  Wolverhampton Wanderers  
date                                                               
2003-08-16               0             0                        0  
2003-08-17               0             0                        0  
2003-08-23               0  

In [23]:
bcr.bar_chart_race(df = SumScenario, 
                   filename = None,
                   period_label = {'x':.75, 'y': .1},
                   n_bars=6,
                   period_length=150,
                   filter_column_colors = 'True',
                   title = 'Premier Abramovich Era')

C:\ProgramData\Anaconda3\lib\site-packages\bar_chart_race\_make_chart.py:286: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_yticklabels(self.df_values.columns)
C:\ProgramData\Anaconda3\lib\site-packages\bar_chart_race\_make_chart.py:287: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_xticklabels([max_val] * len(ax.get_xticks()))


Caso queiramos colocar o dataframe no flourish para uma melhor visualização e personalizar, podemos utlizar o dataframe criado para filtrar os melhores times e salvar como arquivo ".csv"

In [64]:

AcumulateTableS.to_csv("Premier_To_Flourish.csv")

In [25]:
import gc
gc.collect()

15

In [32]:
ScenarioSave = SumScenario.T

In [33]:
ScenarioSave.to_csv("Chelsea_Flourish.csv")